In [1]:
import requests
import os
import json
import http.client
import random
import datetime

# uncomment if needed
# os.environ['HTTP_PROXY']="proxy.vlaanderen.be:8080"
# os.environ['HTTPS_PROXY']="proxy.vlaanderen.be:8080"

## Certificaten

In [11]:
# configureer hieronder het path naar je certificaat en het bestand met je private key. 
# Geef ook de ID van je organisatie (als databeheerder/partner). 

# bestand met je private key
PATH_PKEY = r"C:\Users\pannemba\.ssh\sleutel_voor_VO_instruments\Bart_bij_VO.pem"

# Certificaat OEFEN-omgeving
PATH_CERT = r"C:\Users\pannemba\.ssh\sleutel_voor_VO_instruments\omgeving.vlaanderen.be-dov-services-oefen-BlueDealBemalingen.crt"

# Certificaat PRODUCTIE-omgeving
PATH_CERT_PROD = r"C:\Users\pannemba\.ssh\sleutel_voor_VO_instruments\omgeving.vlaanderen.be-dov-services-productie-BlueDealBemalingen.crt"

# databeheerder ID (VMM="8", dOMG="10")
PARTNER_ID = "10"

## 1. TEST calls
Onderstaande api-endpoints kunnen gebruikt worden om de connectiviteit en de werking van de certificaten te testen. 

In [14]:
# OEFEN-omgeving
request_url = "https://services-oefen.dov.vlaanderen.be/dovinstrumentserver/chucknorris" # werkt niet met fout certificaat, werkt wel zonder certificaat (correcte response = 'Chuck Norris is the reason...')
request_url = "https://services-oefen.dov.vlaanderen.be/dov-xdov-server/logs/count"      # werkt enkel wie rechten heeft op XML (correcte response = {'count': 2400})
request_url = "https://services-oefen.dov.vlaanderen.be/dovkernserver/actoren/0"         # werkt voor wie rechten heeft op instrumenten (correcte response = een actorobject {"id": "0", "naam": "system", "voornaam": null, ...})

response = requests.get(request_url, cert=(PATH_CERT, PATH_PKEY), headers={"Content-Type": "application/json"})
response.text

'Chuck Norris is the reason Waldo is hiding.'

In [8]:
# PRODUCTIE-omgeving
request_url = "https://services-oefen.dov.vlaanderen.be/dovinstrumentserver/chucknorris" # werkt niet met fout certificaat, werkt wel zonder certificaat (correcte response = 'Chuck Norris is the reason...')
request_url = "https://services.dov.vlaanderen.be/dovinstrumentserver/chucknorris"       # werkt altijd, ook zonder certificaat (correcte response = 'Chuck Norris is the reason...')
request_url = "https://services.dov.vlaanderen.be/dov-xdov-server/logs/count"            # werkt enkel wie rechten heeft op XML (correcte response = {'count': 2400})
request_url = "https://services.dov.vlaanderen.be/dovkernserver/actoren/0"               # werkt voor wie rechten heeft op instrumenten (correcte response = een actorobject {"id": "0", "naam": "system", "voornaam": null, ...})

response = requests.get(request_url, cert=(PATH_CERT_PROD, PATH_PKEY), headers={"Content-Type": "application/json"})
response.text

'{"id":"0","naam":"system","voornaam":null,"telnr":null,"gsmnr":null,"faxnr":null,"email":null,"accreditatie":null,"afdeling":"DOV","bedrijf":null,"functie":null,"gemeente":null,"postcode":null,"straat":null,"huisnummer":null,"actief":true}'

## 2. Aanmaken en koppelen van een Gazondolk

In [143]:
# Onderstaand voorbeeld werkt voor een gazondolk
# foutmeldingen:
#    * Dubbele referentie -> Referentie moet uniek zijn binnen organisatie",{"msg":"Er bestaat reeds een instrument met serienummer \
#    * referentie leeg of "" -> GEEN PROBLEEM, dit lukt
#    * Dubbele serienummer -> Er bestaat reeds een instrument met serienummer \"BPA1235\"
#    * Dubbele naam -> GEEN PROBLEEM, dit lukt.
#    * databheerder = 8 ipv 10 -> Access is denied
#    * datum in gebruik: kan zowel met als zonder uur zijn
#    * datum in gebruik: indien geen geldige datum -> JSON parse error: Cannot deserialize value of type [null] from String "": not a valid representation (error: Unparseable date
#    * fout instrumenttype -> Instrumenttype met code "TMS2" kon niet gevonden worden bij DOV
#    * fout typenummer -> Typenummer met code "TMS43" kon niet gevonden worden bij DOV.
#    * fout transmissie ->Transmissie met code "MAN3" kon niet gevonden worden bij DOV.

request_url = "https://services-oefen.dov.vlaanderen.be/hfmetingen/instrumenten/"

voorbeeld = {
            "metadata": {
                "naam": "bart_test_dolk_imdc3",
                "type": {
                    "code": "TMS"
                },
                "serienummer": "BPA1236",
                "referentie": "CN: " + "bart_test_dolk4",
                "datumInGebruik": "2020-01-01", 
                "typeNummer": {
                    "code": "TMS4"
                },
                "transmissie": {
                    "code": "MAN"
                }
            },
            "objectBeheer": {
                "status": {
                    "code": "4"
                },
                "databeheerder": {
                    "id": PARTNER_ID
                }
            },
            "compensatieData": {},
            "sensorData": {
                "sensoren": [
                    {
                        "naam": "SWC",
                        "parameter": {
                            "id": 1912
                        },
                        "sensorIdentificatie": {
                            "code": "CN_SWC"
                        },
                        "meeteenheid": {
                            "code": 127
                        }
                    },
                    {
                        "naam": "T1",
                        "parameter": {
                            "id": 1911
                        },
                        "sensorIdentificatie": {
                            "code": "CN_T1"
                        },
                        "meeteenheid": {
                            "code": 3
                        }
                    },
                    {
                        "naam": "T2",
                        "parameter": {
                            "id": 1911
                        },
                        "sensorIdentificatie": {
                            "code": "CN_T2"
                        },
                        "meeteenheid": {
                            "code": 3
                        }
                    },
                    {
                        "naam": "T3",
                        "parameter": {
                            "id": 1911
                        },
                        "sensorIdentificatie": {
                            "code": "CN_T3"
                        },
                        "meeteenheid": {
                            "code": 3
                        }
                    }
                ]
            }
        }
response = requests.post(request_url, cert=(PATH_CERT, PATH_PKEY), headers={"Content-Type": "application/json", "Accept" : "application/json"},
                         json=voorbeeld)
print(response.text)

{"id":5080,"permKey":"2020-004908","metadata":{"id":5080,"naam":"bart_test_dolk_imdc3","type":{"code":"TMS","beschrijving":"Gazondolk"},"serienummer":"BPA1236","referentie":"","datumInGebruik":"2020-01-01","datumUitGebruik":null,"typeNummer":{"code":"TMS4","beschrijving":"Temperature Moisture Sensor versie 4","merk":{"code":"TOMST","beschrijving":"TOMST","fabrikant":{"code":"TOMST","beschrijving":"TOMST"}},"instrumentType":{"code":"TMS-4","beschrijving":"Temperature Moisture Sensor - Datalogger"}},"locatieStatus":null,"batterijLaatstVervangen":null,"transmissie":{"code":"MAN","beschrijving":"Manueel"}},"objectBeheer":{"id":5139,"status":{"code":"4","beschrijving":"Publiek"},"databeheerder":{"id":"10","kbonummer":null,"ovocode":null,"naam":"dOMG"}},"sensorData":{"instrument":{"id":"5080","permKey":"2020-004908","domainObjectType":null,"naam":"bart_test_dolk_imdc3","objectBeheer":{"id":5139,"status":{"code":"4","beschrijving":"Publiek"},"databeheerder":{"id":"10","kbonummer":null,"ovocod

In [140]:
# Onderstaand voorbeeld werkt voor een gazondolk (onder naam van dOMG, met certificaat van Blue Deal)
# foutmeldingen:
#   * overlappend interval -> Het interval van de koppeling voor deze bodemlocatie mag niet overlappen met een interval van een andere koppeling met deze bodemlocatie

INSTRUMENT_PERMKEY = "2020-004906"
BODEMLOCATIE_PERMKEY = "2022-030448"

request_url = "https://services-oefen.dov.vlaanderen.be/hfmetingen/instrumentlink/"

voorbeeld = {
            "objectType": "BODEMLOCATIE",
            "instrument": {
                "permKey": INSTRUMENT_PERMKEY
            },
            "bodemObjectLinkMetadataDto": {
                "bodemobject": {
                    "permKey": BODEMLOCATIE_PERMKEY
                },
                "startDiepte" : -10,
                "eindDiepte": 13,
                "koppelnaam": "barttest-01",
                "van": "01-11-2022 08:00:00",
                "tot": None,
                "status" : {
                    "code": "4"
                }
            },
            "partner": PARTNER_ID,
            "securityStatus": "PUBLIEK"
        }
response = requests.post(request_url, cert=(PATH_CERT, PATH_PKEY), headers={"Content-Type": "application/json", "Accept" : "application/json"},
                         json=voorbeeld)
print(response.text)

{"objectType":"BODEMLOCATIE","instrument":{"id":"5078","permKey":"2020-004906","domainObjectType":null,"naam":null,"objectBeheer":{"id":5137,"status":{"code":"4","beschrijving":"Publiek"},"databeheerder":{"id":"10","kbonummer":null,"ovocode":null,"naam":"dOMG"}}},"filterObjectLinkMetadataDto":null,"bodemObjectLinkMetadataDto":{"id":7610,"koppelnaam":"barttest-01","van":"01-11-2022 08:00:00","tot":null,"status":{"code":"4","beschrijving":"Publiek"},"bodemobject":{"partner":"10","securityStatus":"PUBLIEK","id":"33871","name":"CN_286946_2022","permKey":"2022-030448","displayName":"CN_286946_2022","type":"BODEM_LOCATIE","revisieId":null},"startDiepte":-10.0,"eindDiepte":13.0,"businessKey":"barttest-01[bodemlocatie:CN_286946_2022]"},"partner":"10","securityStatus":"PUBLIEK","businessKey":"barttest-01[bodemlocatie:CN_286946_2022]"}


## 3. Aanmaken en koppelen van een Diver 

In [145]:
# INSTRUMENT AANMAKEN
# Onderstaand voorbeeld werkt voor een diver (onder naam van dOMG, met certificaat van Blue Deal)
# foutmeldingen:
#    * alle beschrijvingen mogen worden weggelaten. Dit is hier de minimale hoeveelheid die moet worden doorgegeven. 

request_url = "https://services-oefen.dov.vlaanderen.be/hfmetingen/instrumenten/"

voorbeeld = {
    "metadata": {
        "naam": "bart_test_diver_imdc1",
        "type": {
            "code": "Diver",
        },
        "serienummer": "BPA_1234",
        "referentie": "",
        "datumInGebruik": "2022-05-02",
        "typeNummer": {
            "code": "11110304",
        },
        "transmissie": {
            "code": "GPRS",
        }
    },
    "objectBeheer": {
        "status": {
            "code": "4",
        },
        "databeheerder": {
            "id": PARTNER_ID,
        }
    },
    "sensorData": {
        "sensoren": [{
            "naam": "Waterpeil",
            "parameter": {
                "id": "1914",
            },
            "meeteenheid": {
                "code": "200",
            }
        }]
    },
    "compensatieData": {}
}

response = requests.post(request_url, cert=(PATH_CERT, PATH_PKEY), headers={"Content-Type": "application/json", "Accept" : "application/json"},
                         json=voorbeeld)
print(response.text)

{"id":5081,"permKey":"2022-004909","metadata":{"id":5081,"naam":"bart_test_diver_imdc1","type":{"code":"Diver","beschrijving":"Diver"},"serienummer":"BPA_1234","referentie":"","datumInGebruik":"2022-05-02","datumUitGebruik":null,"typeNummer":{"code":"11110304","beschrijving":"TEST - 11110304","merk":{"code":"CERA","beschrijving":"TEST - CERA-Diver","fabrikant":{"code":"EIJK","beschrijving":"TEST - Eijkelkamp"}},"instrumentType":null},"locatieStatus":null,"batterijLaatstVervangen":null,"transmissie":{"code":"GPRS","beschrijving":"GPRS"}},"objectBeheer":{"id":5140,"status":{"code":"4","beschrijving":"Publiek"},"databeheerder":{"id":"10","kbonummer":null,"ovocode":null,"naam":"dOMG"}},"sensorData":{"instrument":{"id":"5081","permKey":"2022-004909","domainObjectType":null,"naam":"bart_test_diver_imdc1","objectBeheer":{"id":5140,"status":{"code":"4","beschrijving":"Publiek"},"databeheerder":{"id":"10","kbonummer":null,"ovocode":null,"naam":"dOMG"}}},"sensoren":[{"id":19087,"permKey":"2022-0

In [8]:
# LINK MAKEN
# Verwijder eventueel eerst de bestaande koppeling uit een vorige test via https://oefen.dov.vlaanderen.be/data/instrument/2022-004909 

# foutmeldingen:
#   * overlappend interval -> Het interval van de koppeling voor deze bodemlocatie mag niet overlappen met een interval van een andere koppeling met deze bodemlocatie
#   * referentie -> referentie met code 1 kon niet gevonden worden bij DOV
#        * oplossing: referentie weglaten -> werkt ook niet -> Referentie moet ingevuld zijn indien ophanglengte is ingevuld."
#        * oplossing: referentie en ophanglengte weglaten -> DIT WERKT!!
#   * koppelnaam niet ingevuld -> foutboodschap: 'Het veld mag niet leeg zijn'
INSTRUMENT_PERMKEY = "2022-004909" 
FILTER_PERMKEY = "2023-105640" # BPA_001 filter 2

request_url = "https://services-oefen.dov.vlaanderen.be/hfmetingen/instrumentlink/"

voorbeeld = {
            "objectType": "FILTER",
            "instrument": {
                "permKey": INSTRUMENT_PERMKEY
            },
            "filterObjectLinkMetadataDto": {
                "filter": {
                    "permKey": FILTER_PERMKEY
                },
                "koppelnaam": "barttest-01",
                "van": "01-06-2023 08:00:00",
                "tot": None,
                "status" : {
                    "code": "4"
                },
                # "ophangLengte" : 6.0,
                # "referentie" : {
                #     "code" : "1"
                # },
            },
            "partner": PARTNER_ID,
            "securityStatus": "PUBLIEK"
        }

response = requests.post(request_url, cert=(PATH_CERT, PATH_PKEY), headers={"Content-Type": "application/json", "Accept" : "application/json"},
                         json=voorbeeld)
print(response.text)

{"objectType":"FILTER","instrument":{"id":"5081","permKey":"2022-004909","domainObjectType":null,"naam":null,"objectBeheer":{"id":5140,"status":{"code":"4","beschrijving":"Publiek"},"databeheerder":{"id":"10","kbonummer":null,"ovocode":null,"naam":"dOMG"}}},"filterObjectLinkMetadataDto":{"id":7637,"koppelnaam":"barttest-01","van":"01-06-2023 08:00:00","tot":null,"status":{"code":"4","beschrijving":"Publiek"},"filter":{"id":"108165","filternummer":"2","grondwaterLocatieId":"104714","exploitantNaam":null,"filterKey":"filter-1678088664594","filterTypeCode":"1","organisatieCode":"10","statusCode":"4","permKey":"2023-105640","grondwaterLocatie":{"@class":"be.vlaanderen.dov.domain.base.put.dto.GrondwaterLocatieDto","id":"104714","identificatie":"BPA_001","grondwaterLocatieKey":"put-1655284304129","organisatieCode":"10","grondwaterlocatieType":"PEILPUT","statusCode":"4","permKey":"2022-101201","exploitantPutNaam":null,"grondwaterLocatieNamen":[]}},"ophangLengte":null,"referentie":null,"busine

In [30]:
# LINK UPDATEN

# foutmeldingen:
#   * method PUT not supported: linkid ontbreekt in url
#   * null: linkid ontbreekt in json (of staat verkeerd genest in de json)
#   * Unable to find be.vlaanderen.dov.instrument.entity.objectlink.InstrumentObjectLink with id 9000: linkid juist meegegeven (dus 2x), maar ongekend.

INSTRUMENT_PERMKEY = "2022-004909" 
FILTER_PERMKEY = "2023-105640" # BPA_001 filter 2
LINK_ID = 7637

request_url = "https://services-oefen.dov.vlaanderen.be/hfmetingen/instrumentlink/%s?comment=Update%%20link" % LINK_ID

voorbeeld = {
            "objectType": "FILTER",
            "instrument": {
                "permKey": INSTRUMENT_PERMKEY,
            },
            "filterObjectLinkMetadataDto": {
                "filter": {
                    "permKey": FILTER_PERMKEY,
                },
                "id": LINK_ID,
                "koppelnaam": "barttest-01",
                "van": "01-06-2023 07:00:00",
                "tot": None,
                "status": {
                    "code": "4",
                }
            },
            "partner": "10",
            "securityStatus": "PUBLIEK"
        }
response = requests.put(request_url, cert=(PATH_CERT, PATH_PKEY), headers={"Content-Type": "application/json", "Accept" : "application/json"},
                         json=voorbeeld)
print(response.text)

https://services-oefen.dov.vlaanderen.be/hfmetingen/instrumentlink/7637?comment=Update%20link
{"objectType":"FILTER","instrument":{"id":"5081","permKey":"2022-004909","domainObjectType":null,"naam":null,"objectBeheer":{"id":5140,"status":{"code":"4","beschrijving":"Publiek"},"databeheerder":{"id":"10","kbonummer":null,"ovocode":null,"naam":"dOMG"}}},"filterObjectLinkMetadataDto":{"id":7637,"koppelnaam":"barttest-01","van":"01-06-2023 07:00:00","tot":null,"status":{"code":"4","beschrijving":"Publiek"},"filter":{"id":"108165","filternummer":"2","grondwaterLocatieId":"104714","exploitantNaam":null,"filterKey":"filter-1678088664594","filterTypeCode":"1","organisatieCode":"10","statusCode":"4","permKey":"2023-105640","grondwaterLocatie":{"@class":"be.vlaanderen.dov.domain.base.put.dto.GrondwaterLocatieDto","id":"104714","identificatie":"BPA_001","grondwaterLocatieKey":"put-1655284304129","organisatieCode":"10","grondwaterlocatieType":"PEILPUT","statusCode":"4","permKey":"2022-101201","explo

## 4. Upload van loggermetingen/peilmetingen
Het opladen van loggermetingen naar DOV gebeurt in twee stappen:  
* *stap 1*: omzetten van de data uit je eigen formaat in het DOV-formaat. Het DOV-formaat kan zowel in CSV als in JSON zijn.   
Deze stap wordt hier niet uitgewerkt, omdat hij afhangt van het vertrekformaat van je eigen data (uit bv. bestanden of uit een database). Er wordt wel een codesnippet voorzien die een dummie CSV-bestand en JSON-records aanmaakt, die gebruikt kan worden als testinput in de volgende stap. 
* *stap 2*: opladen van het CSV/JSON-bestand naar DOV. Er zijn een aantal mogelijkheden, die hieronder elk worden uitgewerkt:  
    * manuele upload van CSV via de webtoepassing,
    * automatische upload van CSV-bestand via een API-postrequest (asynchroon via jobqueue)
    * automatische upload van JSON-body via de API-Post-request (asynchroon via jobqueue)
    * automatische upload van JSON-body met 1 enkele meting via API-post-request (ogenblikkelijke verwerking)
Het is aan de databeheeder om te kijken welke optie meest aansluit bij zijn manier van werken. 

In [10]:
# lijst opvragen van sensoren bij 1 filter
# dit heb je nodig om de permkley van de sensor terug te vinden. 
INSTRUMENT_PERMKEY = "2022-004910" # testdiver aangemaakt door BPA via certificaat

request_url = "https://services-oefen.dov.vlaanderen.be/hfmetingen/instrumenten/%s/sensoren/" % INSTRUMENT_PERMKEY

response = requests.get(request_url, cert=(PATH_CERT, PATH_PKEY), headers={"Content-Type": "application/json", "Accept" : "application/json"})
print(response.text)

[{"code":"2022-019003","beschrijving":"Waterpeil"}]


In [23]:
# STAP 1: aanmaken van CSV-bestand en JSON-records (apart uit te werken, hier wordt enkel een voorbeeldbestandje gemaakt)
# je kan bv een extern script gebruiken om de data uit je eigen database te halen en in het gevraagde CSV- of JSON-formaat te zetten. 
# beschrijving CSV-formaat:
# - er is geen hoofdingrij, elke rij bestaat uit drie komma gescheiden velden. 
# - veld 1: datum in formaat yyyy-MM-dd'T'HH:mm:ss.SSSXXX
# - veld 2: meetwaarde als getal
# - veld 3: gevalideerd of niet: 0 = niet gevalideerd, 1 = gevalideerd
# - voorbeeld: 2018-08-29T00:00:01.000+01:00,20.1,1
# Via de API kan je ook via een JSON-formaat opladen. 
FILE_LOGGER_MEASUREMENTS = "peilmetingen_dummies.csv"

csvrecords = []
jsonrecords = []
nu = datetime.datetime.now()
for i in range(5):
    mytime = datetime.datetime.strftime(nu + datetime.timedelta(hours=i), format="%Y-%m-%dT%H:%M:%S.000+01:00")
    myvalue = round(random.uniform(15, 24),3)
    csvrecords.append("%s,%s,0" % (mytime,myvalue))
    jsonrecords.append({"tijd": mytime, "waarde": myvalue, "status": "GEVALIDEERD"})
print("\n".join(csvrecords))
print(jsonrecords)
with open(FILE_LOGGER_MEASUREMENTS, "w") as outf:
    outf.write("\n".join(csvrecords))

2023-06-23T17:50:49.000+01:00,15.602,0
2023-06-23T18:50:49.000+01:00,23.142,0
2023-06-23T19:50:49.000+01:00,18.024,0
2023-06-23T20:50:49.000+01:00,21.161,0
2023-06-23T21:50:49.000+01:00,21.748,0
[{'tijd': '2023-06-23T17:50:49.000+01:00', 'waarde': 15.602, 'status': 'GEVALIDEERD'}, {'tijd': '2023-06-23T18:50:49.000+01:00', 'waarde': 23.142, 'status': 'GEVALIDEERD'}, {'tijd': '2023-06-23T19:50:49.000+01:00', 'waarde': 18.024, 'status': 'GEVALIDEERD'}, {'tijd': '2023-06-23T20:50:49.000+01:00', 'waarde': 21.161, 'status': 'GEVALIDEERD'}, {'tijd': '2023-06-23T21:50:49.000+01:00', 'waarde': 21.748, 'status': 'GEVALIDEERD'}]


In [20]:
# STAP 2 - optie 1: manueel opladen van het csv bestand via de webinterface. 
# - open het portaal en log in: https://oefen.dov.vlaanderen.be/portaal
# - ga naar Beheer > Beheer instrumenten
# - open het instrument waarvoor je data wilt opladen, door op de naam ervan te klikken
# - ga naar tabblad Sensoren
# - vink de sensor aan waarvoor je data wilt opladen, en klik op de knop 'Acties > voeg data toe'. 
# - sleep het bestand naar het vakje 'bestand toevoegen' (rechtsboven in de popup), en klik op de knop 'Registreer'
# - de upload is geregistreerd. Je kan nu wachten (ca. 10 minuten), of je klikt op 'OK' om de popup af te sluiten.
# - je kan achteraf altijd de status van de laatste upload opvragen door de sensor aan te vinken en dan te klikken op de knop 'Acties > status laatste import'

In [28]:
# STAP 2 - optie 2: opladen van het csv bestand via de API -> dit kan even duren, afhankelijk van de drukte in de verwerkingsqueue
SENSOR_PERMKEY = "2022-019003"

request_url = "https://services-oefen.dov.vlaanderen.be/hfmetingen/instrumenten/%s/sensoren/%s/meetpunten" % (INSTRUMENT_PERMKEY, SENSOR_PERMKEY)

response = requests.post(request_url, cert=(PATH_CERT, PATH_PKEY),
                         files={"file": open(FILE_CSV_MEASUREMENTS, mode="rb")})
print(response.text) # status moet "ASYNC" terug geven!
idcsvbestand = response.json()['importLogId']

https://services-oefen.dov.vlaanderen.be/hfmetingen/instrumenten/2022-004910/sensoren/2022-019003/meetpunten
{"status":"ASYNC","aantal":1,"foutmelding":"","importLogId":32175}


In [29]:
# STAP 2 - optie 3: opladen van json body via de API -> 1 datapunt: ogenblikkelijk
SENSOR_PERMKEY = "2022-019003"

request_url = "https://services-oefen.dov.vlaanderen.be/hfmetingen/instrumenten/%s/sensoren/%s/meetpunten" % (INSTRUMENT_PERMKEY, SENSOR_PERMKEY)

mytime = datetime.datetime.strftime(datetime.datetime.now(), format="%Y-%m-%dT%H:%M:%S.000+01:00")
myvalue = round(random.uniform(15, 24),3)
voorbeeld = [{"tijd": mytime, "waarde": myvalue, "status": "GEVALIDEERD"}]

response = requests.post(request_url, cert=(PATH_CERT, PATH_PKEY),
                         json = voorbeeld)
print(response.text) # status moet "OK" terug geven!

{"status":"OK","aantal":1,"foutmelding":"","importLogId":null}


In [30]:
# STAP 2 - optie 4: opladen van json body via de API -> meerdere datapunt: via de queue (dit kan even duren, afhankelijk van de drukte in de verwerkingsqueue)
SENSOR_PERMKEY = "2022-019003"

request_url = "https://services-oefen.dov.vlaanderen.be/hfmetingen/instrumenten/%s/sensoren/%s/meetpunten" % (INSTRUMENT_PERMKEY, SENSOR_PERMKEY)

mytime = datetime.datetime.strftime(datetime.datetime.now(), format="%Y-%m-%dT%H:%M:%S.000+01:00")
myvalue = round(random.uniform(15, 24),3)
voorbeeld = jsonrecords

response = requests.post(request_url, cert=(PATH_CERT, PATH_PKEY),
                         json = voorbeeld)
print(response.text) # status moet "ASYNC" terug geven!

{"status":"ASYNC","aantal":5,"foutmelding":"","importLogId":32177}


## 5. Upload van manuele peilmetingen (via XML-bestanden)
Er zijn vier stappen nodig:
* Stap 1: aanmaken van een XML-bestand met de peilmetingen. Wordt hier niet uitgewerkt. Een voorbeeld is te vinden op https://www.milieuinfo.be/confluence/display/DDOV/Voorbeelden+XML-bestanden#VoorbeeldenXMLbestanden-XMLvanpeilmetingen
* Stap 2: opladen van het XML-bestand naar de DOV-server. Als dit lukt, krijg je een ID terug van het opgeladen bestand. Dit wordt gebruikt in de volgende stappen. 
* Stap 3: (optioneel en niet echt noodzakelijk): valideren of het opgeladen bestand geldig is.
* Stap 4: importeren van het XML-bestand in DOV. Hierbij wordt het reeds opgeladen bestand effectief in de verwerkingsrij gezet. Zodra er verwerkingscapaciteit beschikbaar is, wordt het dan verwerkt en wordt de data ingeladen in DOV. 
Noot: stap 2 tot 4 kunnen ook manueel gebeuren via het DOV-portaal. Hier wordt enkel de automatische manier gedemonstreerd via de API-endpoints. 

In [12]:
# Stap 2: testen of het opladen van een xml-bestand werkt. 
# correcte resultaat is: {"id":"11391744","naam":"peilmeting.xml"}. Opgelet: dit is enkel opladen, nog niet 'importeren', dus je vindt het niet terug in de lijst van imports

FILE_MANUAL_MEASUREMENTS = "peilmeting.xml"

request_url = "https://services-oefen.dov.vlaanderen.be/dov-xdov-server/import/upload"

response = requests.post(request_url, cert=(PATH_CERT, PATH_PKEY),
                         files={"file": open(FILE_MANUAL_MEASUREMENTS, mode="rb")})
print(response.text)
ID_XMLBESTAND = response.json()['id']

{"id":"11416935","naam":"peilmeting.xml"}


In [29]:
# Stap 3: testen of het valideren van een opgeladen xml-bestand werkt. 
# correcte resultaat is: 
# {"details":[{"id":"7","context":null,"status":{"code":"7","beschrijving":"validatie zonder fouten","id":"7",
# "historyDisplayValue":"7|validatie zonder fouten"},"messages":[],"importObjectPermkey":null,
# "identificatie":"Peilmetingen voor peilfilter 4-0085-2","filtermetingParentType":null,"filtermetingParentId":null}],
# "summary":{"items":[{"option":{"code":"62","beschrijving":null,"id":"62","historyDisplayValue":null},"numberOfObjects":1,
# "id":"62"}],"id":null}}

# vastgestelde foutmeldingen:
# - foute schema gebruikt: complexe json response met ergens erin de boodschap "Exception=Het schema wordt niet ondersteund.be.vlaanderen.dov.schemas.kern.DovSchemaType" -> switch 'invoerwijze' intern <-> edov
# - fout in XML: een lijst met fouten wordt teruggegeven (wel in complexe json) -> consulteer XML-schema om te kijken wat er precies ontbreekt.
# - geen certificaat meegegeven -> dit werkt zonder problemen
# - verkeerde certificaat meegegeven (bv prod vs oefen) -> 403 error.

# opgelet: een boorbedrijf kan momenteel enkel putten en filters aanmaken via XML, maar nog geen peilmetingen toevoegen. Dit wordt binnenkort rechtgetrokken. 
# Voorlopig kunnen boorbedrijven peilmetingen enkel manueel aanleveren via DOV-portaal

# ID_XMLBESTAND = "11413926"
print(ID_XMLBESTAND)

request_url = "https://services-oefen.dov.vlaanderen.be/dov-xdov-server/import/validate"

voorbeeld = {
  # "omschrijving": "opladen XML",
  "invoerwijze": {
    "code": "1",
    # "beschrijving": "intern"
  },
  # "invoerwijze": {  # te gebruiken door boorbedrijven.
  #   "code": "2",
  #   "beschrijving": "edov"
  # },
  "options": [
    {
      "propertyValue": "true",
      "property": {
        "code": "62",
      }
    }
  ],
  "bestand": {
    "id": ID_XMLBESTAND,
  }
}

response = requests.post(request_url, cert=(PATH_CERT, PATH_PKEY),
                         json = voorbeeld)
print(response.text)

11413956
{"details":[{"id":"7","context":null,"status":{"code":"7","beschrijving":"validatie zonder fouten","id":"7","historyDisplayValue":"7|validatie zonder fouten"},"messages":[],"importObjectPermkey":null,"identificatie":"Peilmetingen voor peilfilter 4-0085-2","filtermetingParentType":null,"filtermetingParentId":null}],"summary":{"items":[{"option":{"code":"62","beschrijving":null,"id":"62","historyDisplayValue":null},"numberOfObjects":1,"id":"62"}],"id":null}}


In [31]:
# Stap 4: testen of het importeren werkt. 
# correcte resultaat is: zelfde json, maar met ID ingevuld.
# vastgestelde foutmeldingen:
# - er zijn drie extra velden nodig: omschrijving, gebruikersnaam (mag eenders wat zijn) en status (best 1 = niet verwerkt). Indien die niet
#   aanwezig zijn -> foutmelding: [14-06-361F1C14] : could not execute statement; SQL [n/a]; constraint [gebruikersnaam" of relation 
#   "tbl_invoermetadata]; nested exception is org.hibernate.exception.ConstraintViolationException: could not execute statement
# - bestand werd reeds opgeladen en is niet meer beschikbaar -> foutmelding: [14-06-9559F4CF] : could not execute statement; SQL [n/a]; constraint [uq_tbl_invoermetadata_bestand]; nested exception

# ID_XMLBESTAND = "11413926"
print(ID_XMLBESTAND)

request_url = "https://services-oefen.dov.vlaanderen.be/dov-xdov-server/import"

voorbeeld = {
  "omschrijving": "opladen XML",
  "gebruikersnaam": "Average Rob",  # vrij te kiezen string
  "invoerwijze": {
    "code": "1",
    "beschrijving": "intern"
  },
  "status": {
    "code": "1"  # = niet verwerkt
  },
  "options": [
    {
      "id": None,
      "propertyValue": "true",
      "property": {
        "code": "62",
      }
    }
  ],
  "bestand": {
    "id": ID_XMLBESTAND,
  }
}

response = requests.post(request_url, cert=(PATH_CERT, PATH_PKEY),
                         json = voorbeeld)
print(response.text)

11413956
[14-06-23B2ED99] : could not execute statement; SQL [n/a]; constraint [uq_tbl_invoermetadata_bestand]; nested exception is org.hibernate.exception.ConstraintViolationException: could not execute statement
